# Datos Electorales. ARGENTINA.


In [1]:
# Optimal pandas import
import warnings
warnings.filterwarnings("ignore")
import pandas as pd

pd.options.display.max_colwidth = -1
pd.options.display.max_rows = 999

## Datos de distritos

In [3]:
from unidecode import unidecode

COD_PROV = pd.read_csv('./codigos/COD_PROVINCIAS.csv', ';', encoding = 'latin-1').rename(columns = {'NOMBRE': 'PROVINCIA'})
COD_DEP = pd.read_csv('./codigos/COD_DEPARTAMENTOS.csv', ';', encoding = 'latin-1').rename(columns = {'NOMBRE': 'DEPARTAMENTO'})

COD_PROV['PROV_REF_ID'] = COD_PROV['CODIGO PROVINCIA'].astype(int)#.astype(str)
COD_DEP['PROV_REF_ID'] = COD_DEP['CODIGO PROVINCIA'].astype(int)

#insertar 0 en nombres de comuna, ej. Comuna 05
COD_DEP['dpto_merger_str'] = COD_DEP['DEPARTAMENTO'].str.replace('12 ', 'Doce'
                                            ).str.replace('1° ', 'Primero'
                                            ).str.replace('2 ', 'Dos '
                                            ).str.replace('25', 'Veinticinco'
                                            ).str.replace('9 ', 'Nueve ')

COD_DEP['dpto_merger_str'] = [unidecode(latin_str).lower() for latin_str in COD_DEP['DEPARTAMENTO']]
COD_DEP.loc[:8, 'dpto_merger_str'] = [s[:7] + '0' + s[7:] for s in COD_DEP.loc[:8]['dpto_merger_str'].values]

# Fix differences for BUENOS AIRES dptos
COD_DEP['dpto_merger_str'] = COD_DEP['dpto_merger_str'].str.replace('matanza', 'la matanza'
                                            ).str.replace('j. c. paz', 'jose c. paz'
                                            ).str.replace('roque saenz pena', 'presidente roque saenz pena '
                                            ).str.replace('coronel rosales', 'coronel de marina l. rosales'
                                            ).str.replace('general lamadrid', 'general la madrid'
                                            ).str.replace('las heras', 'general las heras'
                                            ).str.replace('general madariaga', 'general juan madariaga'
                                            ).str.replace('gonzales chaves', 'adolfo gonzales chaves'
                                            ).str.replace('f. ameghino', 'florentino ameghino'
                                            ).str.replace('juarez', 'benito juarez'
                                            ).str.replace('arrecifes', 'bartolome mitre'
                                            ).str.replace('lezama', 'chascomus')

geo_ref = pd.read_csv('./../../Dropbox/PBAshared/data/other/censo_geo/radio_ref.csv')
geo_ref['dpto_merger_str'] = geo_ref['NOMDPTO'].str.replace('12 ', 'Doce'
                                            ).str.replace('1° ', 'Primero'
                                            ).str.replace('2 ', 'Dos '
                                            ).str.replace('25', 'Veinticinco'
                                            ).str.replace('9 ', 'Nueve ')

geo_ref['dpto_merger_str'] = geo_ref['dpto_merger_str'].str.strip()
geo_ref['dpto_merger_str'] = [unidecode(latin_str).lower() for latin_str in geo_ref['dpto_merger_str']]
# geo_ref['dpto_merger_str'] = geo_ref['dpto_merger_str'].str.replace('arrecifes', 'bartolome mitre')

geo_ref.head()

# Las cantidades matchean. Bien!
# Tambien los codigos de provincia.
# geo_ref.groupby('PROV_REF_ID')['DPTO'].nunique()
# COD_DEP.groupby('IDPROV')['DEPARTAMENTO'].nunique()

merged = COD_DEP.merge(geo_ref[['PROV_REF_ID','PROV','DPTO', 'dpto_merger_str']].drop_duplicates(), how = 'left')
merged = merged.dropna() # perdemos dptos no matcheados del interior

IDcols = ['PROV_REF_ID', 'PROV', 'DPTO']
merged[IDcols] = merged[IDcols].applymap(int).applymap(str)


# Las provincias completas son CABA y GBA. Resto del pais hay como 30/350 dptos que no matchean
dpto_ref_BA = merged.loc[merged.PROV_REF_ID.isin(['1', '2'])].set_index('DEPARTAMENTO')[['DPTO', 'dpto_merger_str']]
display(dpto_ref_BA.sample(5))
# Ya esta todo linkeado con DPTOS geo, se pueden hacer mapas.

DPTO         dpto_merger_str
DEPARTAMENTO                                   
SUIPACHA           6784  suipacha              
SAN VICENTE        6778  san vicente           
GENERAL LAMADRID   6322  general la madrid     
GENERAL MADARIAGA  6315  general juan madariaga
NUEVE DE JULIO     6588  nueve de julio

## Data Electoral

### 2015

In [4]:
#Load data

DN_2015 = pd.concat([pd.read_csv('./escrutinio/2015/FMESDN_0101.csv', ';'),
                            pd.read_csv('./escrutinio/2015/FMESDN_0202.csv', ';'),
                            pd.read_csv('./escrutinio/2015/FMESDN_0313.csv', ';'),
                            pd.read_csv('./escrutinio/2015/FMESPR_1424.csv', ';')])
DN_2015['ELECCION'] = 'PV_2015'
# DN_2015.sum()
# Nombres de listas
COD_PARTIDOS = pd.read_csv('./codigos/COD_PARTIDOS_2015.csv', ';', encoding = 'latin-1')[[u'Codigo Partido', u'Denominacion']]
COD_PARTIDOS.columns = [unidecode(col) for col in COD_PARTIDOS.columns] # atender  Esta tilde
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.strip()
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace('ALIANZA CAMBIEMOS', 'CAMBIEMOS')
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace('CAMBIEMOS BUENOS AIRES', 'CAMBIEMOS')

 # mergear
DN_2015 = DN_2015.merge(COD_PARTIDOS, left_on = u'CODIGO VOTOS', right_on = u'Codigo Partido')

# mergear parte geografica
DN_2015 = DN_2015.merge(COD_PROV).merge(COD_DEP, on = ['CODIGO DEPARTAMENTO', u'PROV_REF_ID'])
# #fix
DN_2015.columns = DN_2015.columns.str.strip()
DN_2015['circuito'] = DN_2015['CODIGO CIRCUITO'].astype(str).str.strip().str.zfill(4)


### Cargar Paso 2017

In [5]:
paso_2017 = pd.concat([pd.read_csv('./escrutinio/2017/paso2017-FMESDN_0101.csv', ';'),
                            pd.read_csv('./escrutinio/2017/paso2017-FMESDN_0202.csv', ';'),
                            pd.read_csv('./escrutinio/2017/paso2017-FMESDN_0313.csv', ';'),
                            pd.read_csv('./escrutinio/2017/paso2017-FMESDN_1424.csv', ';')])
paso_2017['ELECCION'] = 'paso_2017'

COD_PARTIDOS = pd.read_csv('./codigos/COD_PARTIDOS_2017_paso.csv', ';', encoding = 'latin-1')[[u'Código Partido', u'Denominacion']]
COD_PARTIDOS.columns = [unidecode(col) for col in COD_PARTIDOS.columns]
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.strip()
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace('CAMBIEMOS BUENOS AIRES', 'CAMBIEMOS')
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace('VAMOS JUNTOS', 'CAMBIEMOS')
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace(u'UNIDAD PORTEÑA', 'UNIDAD CIUDADANA')

paso_2017 = paso_2017.merge(COD_PARTIDOS, left_on = u'CODIGO VOTOS', right_on = u'Codigo Partido')
paso_2017 = paso_2017.merge(COD_PROV).merge(COD_DEP, on = ['CODIGO DEPARTAMENTO', u'PROV_REF_ID'])
# #fix
paso_2017.columns = paso_2017.columns.str.strip()
paso_2017['circuito'] = paso_2017['CODIGO CIRCUITO'].astype(str).str.strip().str.zfill(4)

### Cargar DN 2017

In [6]:

DN_2017 = pd.concat([pd.read_csv('./escrutinio/2017/FMESDN_0101.csv', ';'),
                            pd.read_csv('./escrutinio/2017/FMESDN_0202.csv', ';'),
                            pd.read_csv('./escrutinio/2017/FMESDN_0313.csv', ';'),
                            pd.read_csv('./escrutinio/2017/FMESDN_1424.csv', ';')])
DN_2017['ELECCION'] = 'DN_2017'

COD_PARTIDOS = pd.read_csv('./codigos/COD_PARTIDOS_2017_paso.csv', ';', encoding = 'latin-1')[[u'Código Partido', u'Denominacion']]
COD_PARTIDOS.columns = [unidecode(col) for col in COD_PARTIDOS.columns]
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.strip()
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace('CAMBIEMOS BUENOS AIRES', 'CAMBIEMOS')
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace('VAMOS JUNTOS', 'CAMBIEMOS')
COD_PARTIDOS['Denominacion'] = COD_PARTIDOS['Denominacion'].str.replace(u'UNIDAD PORTEÑA', 'UNIDAD CIUDADANA')

DN_2017 = DN_2017.merge(COD_PARTIDOS, left_on = u'CODIGO VOTOS', right_on = u'Codigo Partido')
DN_2017 = DN_2017.merge(COD_PROV).merge(COD_DEP, on = ['CODIGO DEPARTAMENTO', u'PROV_REF_ID'])
# #fix
DN_2017.columns = DN_2017.columns.str.strip()
DN_2017['circuito'] = DN_2017['CODIGO CIRCUITO'].astype(str).str.strip().str.zfill(4)

In [7]:
## Un poquito de numerologia, porque dan muy redondo algunos numeros en la PASO 17 Buenos Aires.

# Cambiemos tiene 20.00% y UC 10.009986% de los votantes.

# (3310366 * 2) - 6555803
# 3310366*0.000001
# 6555803/64929
# 3310366/0.10099 #32776326
# 32776326 - 32775900.99009901
# 3310366/32776326 #0.100999
# 0.10099869033521329 - 0.101
# -1.30966478671668e-06 * 32776326
# 6555803/32776326 #0.200016
# 0.00001640818437064*32776326

## Armar cuadro resumen nacional

In [8]:
# data_eleccion = DN_2017

# total_de_electores = 33502945 # Oct 17
# # total_de_electores = 32776326 # Aug 17
# # total_de_electores = 31754774 # Oct 15

# cuadro_nac = data_eleccion.groupby('Denominacion').sum().sort_values(by = 'VOTOS', ascending = False)#/total_de_electores 
# # SORPRENDENTE. Con paso 17
# # Como puede ser que sean tan redondos los numeros?
# # Estamos hablando de 6555803
# cuadro_nac.head(10)

# Cuadro resumen nacional. Elecciones 2015, p2017 y 2017.

In [9]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [29]:
by_col = ['dpto_merger_str', 'circuito']
results_summary = []

for i, data_eleccion in enumerate([DN_2015, paso_2017, DN_2017]):

    main = [['ELECTORES', 'VOTANTES', 'ALIANZA FRENTE PARA LA VICTORIA', 'CAMBIEMOS',
         'ALIANZA UNIDOS POR UNA NUEVA ALTERNATIVA (UNA)', 'VOTOS BLANCOS',
         'ALIANZA FRENTE DE IZQUIERDA Y DE LOS TRABAJADORES'],
        ['ELECTORES', 'VOTANTES', 'CAMBIEMOS', 'UNIDAD CIUDADANA', '1PAIS',
         'FRENTE JUSTICIALISTA', 'VOTOS BLANCOS',
         'FRENTE DE IZQUIERDA Y DE LOS TRABAJADORES'],
        ['ELECTORES', 'VOTANTES', 'CAMBIEMOS', 'UNIDAD CIUDADANA',
         'FRENTE JUSTICIALISTA', 'FRENTE DE IZQUIERDA Y DE LOS TRABAJADORES',
         '1PAIS', 'VOTOS BLANCOS']][i]
    name = ['DN_2015', 'paso_2017', 'DN_2017'][i]
    ppales_listas = data_eleccion.loc[data_eleccion.Denominacion.isin(main)]
    total_de_electores = data_eleccion.groupby('Denominacion').sum().loc['ELECTORES']['VOTOS']

    # Seleccionar provincias
    ppales_listas_prov = ppales_listas.loc[ppales_listas['PROVINCIA'].isin(['BUENOS AIRES', 'CIUDAD AUTONOMA DE BS.AS.'])]

    cuadro = ppales_listas_prov.groupby(['Denominacion','PROV_REF_ID']+ by_col).sum()[['VOTOS']].sort_values(by = 'VOTOS', ascending = False)
    cuadro = cuadro.unstack([0, 1])

    # Crear tabla porcentual
    cuadro_pct = cuadro.copy()
    cuadro_pct['VOTOS'] = cuadro['VOTOS']/cuadro['VOTOS']['ELECTORES']
    cuadro_pct.columns = cuadro_pct.columns.set_levels(['VOTOS_pct'], level = 0)
    cuadro_pct = pd.concat([cuadro_pct], keys=[name], names=['Eleccion'], axis = 1)

    cuadro = pd.concat([cuadro], keys=[name], names=['Eleccion'], axis = 1)

    results_summary += [pd.concat([cuadro, cuadro_pct], axis = 1)]


results_summary = pd.concat(results_summary, axis = 1)

# if len(by_col) == 2:
#     results_summary = results_summary.stack(-2, -1)
# elif len(by_col) == 1:
#     results_summary = results_summary.stack()

In [30]:
# Ejemplo
import seaborn as sns
cm = sns.light_palette("green", as_cmap=True)

s = results_summary['DN_2017']['VOTOS']
ordenh = s.sum().sort_values(ascending = False).index
ordenv = s.sum(1).sort_values(ascending = False).index
# (100*s)

#order
s = s.reindex(ordenv).reindex(ordenh,axis = 1)
# Append totals
# s = s.append(s.sum(), ignore_index=True)
s.style.background_gradient(cmap=cm, axis = 1)


In [15]:
# Ejemplo
s.to_csv('./tabla_resumen.csv')
s.head()

Denominacion                             ELECTORES  VOTANTES  CAMBIEMOS  \
dpto_merger_str    circuito PROV_REF_ID                                   
lomas de zamora    0583     2            206753.0   146146.0  30975.0     
merlo              0652A    2            139025.0   106765.0  26215.0     
general pueyrredon 0364     2            135506.0   97139.0   42261.0     
                   0365     2            119503.0   85772.0   36660.0     
florencio varela   0302     2            117519.0   85593.0   27853.0     

Denominacion                             UNIDAD CIUDADANA    1PAIS  \
dpto_merger_str    circuito PROV_REF_ID                              
lomas de zamora    0583     2            79523.0           11433.0   
merlo              0652A    2            54533.0           11849.0   
general pueyrredon 0364     2            29383.0           10738.0   
                   0365     2            27866.0           9344.0    
florencio varela   0302     2            35716.0           7384.0    

Denominacion                             FRENTE DE IZQUIERDA Y DE LOS TRABAJADORES  \
dpto_merger_str    circuito PROV_REF_ID                                              
lomas de zamora    0583     2            6156.0                                      
merlo              0652A    2            5980.0                                      
general pueyrredon 0364     2            5178.0                                      
                   0365     2            4782.0                                      
florencio varela   0302     2            4622.0                                      

Denominacion                             FRENTE JUSTICIALISTA  VOTOS BLANCOS  
dpto_merger_str    circuito PROV_REF_ID                                       
lomas de zamora    0583     2            6951.0                5049.0         
merlo              0652A    2            5662.0                3203.0         
general pueyrredon 0364     2            4541.0                3834.0         
                   0365     2            4321.0                3565.0         
florencio varela   0302     2            4363.0                2818.0

In [22]:
## Guardar

In [20]:
results_summary.to_csv('./VOTOS_2015_17_'+by_col[-1][:4]+'.csv')

In [35]:
# como cargarlo
df = pd.read_csv('./VOTOS_2015_17_'+by_col[-1][:4]+'.csv', header = [0, 1, 2], index_col=list(range(len(by_col) + 1)))
df.head()

Eleccion                                                                       DN_2015  \
                                                                                 VOTOS   
Denominacion                         ALIANZA FRENTE DE IZQUIERDA Y DE LOS TRABAJADORES   
dpto_merger_str circuito PROV_REF_ID                                                     
adolfo alsina   0001     2            82.0                                               
                0002     2            1.0                                                
                0003     2            30.0                                               
                0004     2            0.0                                                
                0005     2            7.0                                                

Eleccion                                                              \
                                                                       
Denominacion                         ALIANZA FRENTE PARA LA VICTORIA   
dpto_merger_str circuito PROV_REF_ID                                   
adolfo alsina   0001     2            1798.0                           
                0002     2            6.0                              
                0003     2            598.0                            
                0004     2            6.0                              
                0005     2            171.0                            

Eleccion                                                                             \
                                                                                      
Denominacion                         ALIANZA UNIDOS POR UNA NUEVA ALTERNATIVA (UNA)   
dpto_merger_str circuito PROV_REF_ID                                                  
adolfo alsina   0001     2            698.0                                           
                0002     2            11.0                                            
                0003     2            314.0                                           
                0004     2            4.0                                             
                0005     2            83.0                                            

Eleccion                                                           \
                                                                    
Denominacion                         CAMBIEMOS ELECTORES VOTANTES   
dpto_merger_str circuito PROV_REF_ID                                
adolfo alsina   0001     2            2997.0    8376.0    6714.0    
                0002     2            28.0      89.0      56.0      
                0003     2            971.0     2772.0    2225.0    
                0004     2            16.0      54.0      28.0      
                0005     2            623.0     1194.0    969.0     

Eleccion                                            \
                                                     
Denominacion                         VOTOS BLANCOS   
dpto_merger_str circuito PROV_REF_ID                 
adolfo alsina   0001     2            900.0          
                0002     2            7.0            
                0003     2            261.0          
                0004     2            2.0            
                0005     2            68.0           

Eleccion                                                                                \
                                                                             VOTOS_pct   
Denominacion                         ALIANZA FRENTE DE IZQUIERDA Y DE LOS TRABAJADORES   
dpto_merger_str circuito PROV_REF_ID                                                     
adolfo alsina   0001     2            0.009790                                           
                0002     2            0.011236                                           
                0003     2            0.010823                                           
                0